## This correctly filters out prior indexed ARIS data, January 2023.
### Compares ARIS FY prior Quarter (Qa), current Quarter (Qb) files for duplication, and differences in:
- Accession
- Title
- Objectives
- Approach

#### Step 1. Check for duplicates within each ARS input file type (Projects, Objectives, Approach) across prior Quarter (Qa) and current Quarter (Qb)
#### Step 2. Open each ARS input csv and create a data frame, and append them together into one data frame.
#### Step 3. Generate final output of selected text for accession, title, abstract (objective+approach).

In [47]:
# Imports
import pandas as pd
import os
import glob
import numpy as np
import functools as ft

In [48]:
# Check ARS Project (Titles) input files provided for Qa and Qb. Open each as a list, combine to one
# list, and check for duplicates across Qa and Qb.

print('DATA CHECK: Projects (Titles):') 
with open('A416_Projects_10_03_2022.csv', 'r', encoding='utf-8', errors='ignore') as f:
    dataP = f.readlines()

with open('A416_Projects_01_03_2023.csv', 'r', encoding='utf-8', errors='ignore') as f:
    data2P = f.readlines()

dataP.extend(data2P)
print(type(dataP), len(dataP), len(set(dataP)),'\n')
# print('\nDataProjects:\n', dataP)

DATA CHECK: Projects (Titles):
<class 'list'> 394 209 



In [49]:
# Check ARS Objectives input files provided for Qa and Qb. Open each as a list, combine to one
# list, and check for duplicates across Qa and Qb.

print('DATA CHECK: Objective:')
with open('A416_Objective_10_03_2022.csv', 'r', encoding='utf-8', errors='ignore') as f:
    dataO = f.readlines()

with open('A416_Objective_01_03_2023.csv', 'r', encoding='utf-8', errors='ignore') as f:
    data2O = f.readlines()
    
dataO.extend(data2O)

print(type(dataO), len(dataO), len(set(dataO)))

DATA CHECK: Objective:
<class 'list'> 407 246


In [50]:
# Check ARS Approach input files provided for Qa and Qb. Open each as a list, combine to one
# list, and check for duplicates across Qa and Qb.

print('DATA CHECK: Approach:')
with open('A416_Approach_10_03_2022.csv', 'r', encoding='utf-8', errors='ignore') as f:
    dataA = f.readlines()

with open('A416_Approach_01_03_2023.csv', 'r', encoding='utf-8', errors='ignore') as f:  #, errors='ignore'
    data2A = f.readlines()

dataA.extend(data2A)

print(type(dataA), len(dataA), len(set(dataA)))

DATA CHECK: Approach:
<class 'list'> 396 255


In [51]:
# Open each ARS input csv file and convert to a data frame, add each data frame object to a list of data frames, and
# check how many projects are listed in each for Qa and Qb title, objectives, approach.

dfs = []

print('Data check')
for fname in glob.glob('*.csv'):

    newdf = pd.read_csv(fname, encoding='ISO-8859-1')
    newdf.rename(columns={"Project Number": "Project_Number", "Project Title": "Project_Title"})
#     newdf.columns = [c.replace(' ', '_') for c in newdf.columns]
#     newdf = newdf.Project_Title = newdf.Project_Title + '.'
    print('\n', fname)
    print(type(newdf), len(newdf))
    
    print('\nKeys\n', newdf.keys())
    print('===')
    
    # Accession was giving unicode error - a fix.
    for key in newdf.keys():
        print(key)
        keycheck = len(str(key))
        print('keycheck', keycheck)
        if 'Accession' in key:
            if len('Accession') != keycheck:
                newdf['Accession'] = newdf.pop(key)

    dfs.append(newdf)
            
print(newdf.keys())

Data check

 A416_Objective_01_03_2023.csv
<class 'pandas.core.frame.DataFrame'> 198

Keys
 Index(['ï»¿Accession', 'Objective'], dtype='object')
===
ï»¿Accession
keycheck 12
Objective
keycheck 9

 A416_Approach_01_03_2023.csv
<class 'pandas.core.frame.DataFrame'> 198

Keys
 Index(['ï»¿Accession', 'Approach'], dtype='object')
===
ï»¿Accession
keycheck 12
Approach
keycheck 8

 A416_Approach_10_03_2022.csv
<class 'pandas.core.frame.DataFrame'> 194

Keys
 Index(['ï»¿Accession', 'Approach'], dtype='object')
===
ï»¿Accession
keycheck 12
Approach
keycheck 8

 A416_Objective_10_03_2022.csv
<class 'pandas.core.frame.DataFrame'> 194

Keys
 Index(['ï»¿Accession', 'Objective'], dtype='object')
===
ï»¿Accession
keycheck 12
Objective
keycheck 9

 A416_Projects_10_03_2022.csv
<class 'pandas.core.frame.DataFrame'> 194

Keys
 Index(['ï»¿Accession ', 'Project Number', 'Project Title'], dtype='object')
===
ï»¿Accession 
keycheck 13
Project Number
keycheck 14
Project Title
keycheck 13

 A416_Projects_01_0

In [52]:
# Full analyses of each field accession, project number, title, objectives, approach for differences from Qa to Qb.
# Merge the data frames (ft.reduce), how = outer to grab all accessions in Qa and Qb.
# Create column for boolean values for 'True' if Qa = Qb, or 'False' if Qa does not = Qb for each of these fields.
# DATA CHECK: Print out values for columns generated by Pandas in appending these files, and the added columns so far. 

result = ft.reduce(lambda left, right: pd.merge(left, right, on='Accession', how='outer'), dfs)
result['ProjNumx=y'] = np.where((result['Project Number_x'] == result['Project Number_y']), True, False)
result['Titlex=y'] = np.where((result['Project Title_x'] == result['Project Title_y']), True, False)
result['Objx=y'] = np.where((result['Objective_x'] == result['Objective_y']), True, False)
result['Appx=y'] = np.where((result['Approach_x'] == result['Approach_y']), True, False)

cols = []
for col in result.columns:
    cols.append(col)
print('Data check:\n Columns generated\n', cols)
cols = ['Accession', 'Project Number_x', 'Project Number_y', 'Project Title_x', 'Project Title_y', 
        'Objective_x', 'Objective_y', 'Approach_x', 'Approach_y', 'ProjNumx=y', 'Titlex=y', 'Objx=y', 'Appx=y']

result = result[cols]

Data check:
 Columns generated
 ['Objective_x', 'Accession', 'Approach_x', 'Approach_y', 'Objective_y', 'Project Number_x', 'Project Title_x', 'Project Number_y', 'Project Title_y', 'ProjNumx=y', 'Titlex=y', 'Objx=y', 'Appx=y']


In [53]:
# Based on the boolean analyses above, determine which Quarter to annotate by each field: title, objectives, and approach.
# *2Annot = Where *x=y is True, use Qa(*_x), else check if Qb = null is True, then use Qa (*_x), else use Qb (*_y).

result['Title2Annot'] = np.where((result['Titlex=y'] == True), 
                                 result['Project Title_x'], 
                                 np.where((result['Project Title_y'].isnull()), result['Project Title_x'],
                                          result['Project Title_y']))
result['Obj2Annot'] = np.where((result['Objx=y'] == True), result['Objective_x'], 
                               np.where((result['Objective_y'].isnull()), result['Objective_x'],
                                        result['Objective_y']))
result['App2Annot'] = np.where((result['Appx=y'] == True), 
                               result['Approach_y'],
                                np.where((result['Approach_y'].isnull()), result['Approach_x'], 
                                        result['Approach_y']))


In [54]:
# Record decisions in new 'decision' column, based on boolean logic in ProjNumx=y,Titlex=y, Objx=y, Appx=y.

conditions = [
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == True) & 
    (result['Objx=y'] == True) & (result['Appx=y'] == True),
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == False) & 
    (result['Objx=y'] == True) & (result['Appx=y'] == True),
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == True) & 
    (result['Objx=y'] == False) & (result['Appx=y'] == True),
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == True) & 
    (result['Objx=y'] == True) & (result['Appx=y'] == False),
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == False) & 
    (result['Objx=y'] == False) & (result['Appx=y'] == False),
    (result['ProjNumx=y'] == True) & (result['Titlex=y'] == False) & 
    (result['Objx=y'] == False) & (result['Appx=y'] == True),
    (result['ProjNumx=y'] == False) & (result['Titlex=y'] == False) & 
    (result['Objx=y'] == False) & (result['Appx=y'] == False),
             ]

values = ['useQa', 'ChkTitle', 'ChkObj', 'ChkApp', 'useQb', 'useQbTiOb', 'useQb' ]

result['decision'] = np.select(conditions, values)

In [55]:
# Rename column headers to reflect Qa or Qb data for easier review.
# DATA CHECK datatypes in the data frame.

result = result.rename(columns={'Project Number_x': 'ProjNum_Qa', 'Project Number_y':'ProjNum_Qb', 
                                'Project Title_x':'Title_Qa', 'Project Title_y':'Title_Qb', 
                                'Objective_x':'Obj_Qa', 'Objective_y':'Obj_Qb', 'Approach_x': 'Approach_Qa', 
                                'Approach_y': 'Approach_Qb'})

print('\nData check\n result df data types')
print(result.dtypes)


Data check
 result df data types
Accession       int64
ProjNum_Qa     object
ProjNum_Qb     object
Title_Qa       object
Title_Qb       object
Obj_Qa         object
Obj_Qb         object
Approach_Qa    object
Approach_Qb    object
ProjNumx=y       bool
Titlex=y         bool
Objx=y           bool
Appx=y           bool
Title2Annot    object
Obj2Annot      object
App2Annot      object
decision       object
dtype: object


In [56]:
# Summary report out of duplication in title, objectives, approach field for each accession number.
print('\nFULL SUMMARY Report of Duplicate Analyses')
print('DATA CHECK:\nDuplicate Accessions removed, Qa and Qb title, objectives, approach compared, value = True if same')
print('ARS Headquarters requested annotation for the latest (Qb) data for any fields that differ for each accession number.')

print('\nSUMMARY\nCount of unique Accession numbers:')
print(result.index.value_counts().sum())

count = result["ProjNumx=y"].value_counts()
count
print('\nSUMMARY\nQa vs Qb is identical ("True") Project Numbers count:')
print(count)

count = result["Titlex=y"].value_counts()
count
print('\nSUMMARY\nQa vs Qb is identical ("True") Titles count:')
print(count)

count = result["Objx=y"].value_counts()
count
print('\nSUMMARY\nQa vs Qb is identical ("True") Objectives count:')
print(count)

count = result["Appx=y"].value_counts()
count
print('\nSUMMARY\nQa vs Qb is identical ("True") Approach count:')
print(count)

count = result["decision"].value_counts()
count
print('\nSUMMARY\nuseQtr decisions:')
print(count) 
 


FULL SUMMARY Report of Duplicate Analyses
DATA CHECK:
Duplicate Accessions removed, Qa and Qb title, objectives, approach compared, value = True if same
ARS Headquarters requested annotation for the latest (Qb) data for any fields that differ for each accession number.

SUMMARY
Count of unique Accession numbers:
199

SUMMARY
Qa vs Qb is identical ("True") Project Numbers count:
True     189
False     10
Name: ProjNumx=y, dtype: int64

SUMMARY
Qa vs Qb is identical ("True") Titles count:
True     188
False     11
Name: Titlex=y, dtype: int64

SUMMARY
Qa vs Qb is identical ("True") Objectives count:
True     160
False     39
Name: Objx=y, dtype: int64

SUMMARY
Qa vs Qb is identical ("True") Approach count:
True     140
False     59
Name: Appx=y, dtype: int64

SUMMARY
useQtr decisions:
useQa       115
ChkApp       40
ChkObj       21
0            13
useQb         8
ChkTitle      2
Name: decision, dtype: int64


In [57]:
# Display FULL SUMMARY findings, each quarter data, decisions, and selected text to annotate in the 'result' data frame.
# Pandas df settings to show all data in the jupyter notebook for easier review and data checking.
pd.set_option('display.max_columns', None)
pd.set_option('display.max_colwidth', None)  # or 199
pd.set_option('display.max_rows', None)
pd.set_option('display.width', 1000)
pd.set_option('display.colheader_justify', 'center')
pd.set_option('display.precision', 3)

# result = result.set_index('Accession')
print('\nDATA CHECK: Qa v. Qb data and Decisions')
display(result)


DATA CHECK: Qa v. Qb data and Decisions


Accession      ProjNum_Qa           ProjNum_Qb                                                                                                       Title_Qa                                                                                                                                                                                                   Title_Qb                                                                                                   \
0     438987    5090-21630-001-000D  5090-21630-001-000D                                                                                                                     Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest.                                                                                                                     Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest.   
1     439564    8072-41420-024-000D  8072-41420-024-000D                                                                                             Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction.                                                                                             Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction.   
2     439671    6040-32000-080-000D  6040-32000-080-000D                                                                                                 Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry.                                                                                                 Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry.   
3     440376    8072-42000-092-000D  8072-42000-092-000D                                                                                                                        Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods.                                                                                                                        Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods.   
4     440440    8044-22000-051-000D  8044-22000-051-000D                                                                                                Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens.                                                                                                Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens.   
5     440524    2034-13210-002-000D  2034-13210-002-000D                                                                                                                    Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S.                                                                                                                    Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S.   
6     440529    8072-42000-093-000D  8072-42000-093-000D                                                                                                                       Detection, Quantification and Characterization Technologies for Foodborne Pathogens.                                                                                                                       Detection, Quantification and Characterization Technologies for Foodborne Pathogens.   
7     440677    5030-32000-228-000D  5030-32000-228-000D                                                                                                                Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies.                  

In [58]:
# Generate final output of selected text for accession, title, abstract (objective+approach).
# Save to 'annotation.csv' file for excel indexer (indexer.xmls).

result.to_csv('out/dupe-analyses-result.csv')

# Select most recent (Qa or Qb) title, and objectives, approach to combine for annotation
annotation = result
annotation['Title'] = result['Title2Annot']
annotation['Abstract'] = result['Obj2Annot'] + result['App2Annot']
cols = ['Accession', 'Title', 'Abstract']
annotation = annotation[cols]
annotation = annotation.set_index('Accession')

print('\nDATA CHECK: Final selected data for Annotation')
print('Count of unique Accession numbers:')
print(result.index.value_counts().sum())

annotation.to_csv('out/annotation.csv')

display(annotation)


DATA CHECK: Final selected data for Annotation
Count of unique Accession numbers:
199


Title                                                                                                     \
Accession                                                                                                                                                                                                              
438987                                                                                                                        Improving Sustainability of Dairy and Forage Production Systems for the Upper Midwest.   
439564                                                                                                Incidence of Bacterial Pathogens in Regulated Foods and Applied Processing Technologies for Their Destruction.   
439671                                                                                                    Genomic and Epidemiological Parameters to Inform Interventions Strategies for Enteric Diseases of Poultry.   
440376                                                                                                                           Advanced Methods for Predictive Modeling of Bacterial Growth and Survival in Foods.   
440440                                                                                                   Integrative Genomic and Biological Approaches to Detect and Manage Emerging Foreign Fungal Plant Pathogens.   
440524                                                                                                                       Improved Management, Quality and Utilization of Alfalfa for Dairies in the Western U.S.   
440529                                                                                                                          Detection, Quantification and Characterization Technologies for Foodborne Pathogens.   
440677                                                                                                                   Elucidating the Pathobiology and Transmission of Transmissible Spongiform Encephalopathies.   
440718                                                                                 Innovative Manure Treatment Technologies and Enhanced Soil Health for Agricultural Systems of the Southeastern Coastal Plain.   
440790                                                                                                                                Advancement of Sensing Technologies for Food Safety and Security Applications.   
440891                                                                   Soil, Crop, and Manure Biochemistry and Molecular Ecology: Bridging Knowledge Gaps in Microbiome Response to Management and Climate Change.   
440922                                                                                          Sustainable Management of Manure Nutrients and Environmental Contaminants from Beef and Swine Production Facilities.   
440930                                                                                                                 Holistic Tactics to Advance the Microbiological Safety and Quality of the Red Meat Continuum.   
440948       Analysis of Genetic Factors that Increase Foodborne Pathogen Fitness, Virulence, and Antimicrobial Resistance Transfer, to Identify Interventions against Salmonella and Campylobacter in Food Animals.   
440963                                                                                                                                       Exploration for Natural Enemies in China for Citrus psyllid in the U.S.   
440973     Improving Pre-harvest Produce Safety through Reduction of Pathogen Levels in Agricultural Environments and Development and Validation of Farm-Scale Microbial Quality Model for Irrigation Water Sources.   
441096                                                          Developing Agronomically and Environmentally Beneficial Management Practices to Increase the Sustainability and Safety of Animal Manure Utilization.   
4410

In [59]:
# Generate final output of selected text for never before seen articles, for accession, title, abstract (objective+approach).
# Save to 'newannotation.csv' file for excel indexer (indexer.xmls).

findnewarticlesdf = pd.DataFrame(result, columns = ['Accession', 'Title', 'Abstract', 'decision'])
newarticlesdf = findnewarticlesdf.loc[findnewarticlesdf['decision']=='useQb']

print('\nSUMMARY\nCount of unique Accession numbers:')

print(newarticlesdf.index.value_counts().sum())

display(newarticlesdf)


SUMMARY
Count of unique Accession numbers:
8


Accession                                                                            Title                                                                              \
180   442616                                                                     Intervention Strategies to Control Salmonella and Campylobacter During Poultry Processing.   
190   443180    Enhancing Genetic Resistance and Vaccinal Response to Control MarekÎÃÃs Disease, Infectious Laryngotracheitis, and Infectious Bursal Disease in Chicken.   
192   443259                                                Reducing the Impact of Subclinical Enteric Infections on Performance and Gastrointestinal Function of Broilers.   
194   443340                                                                                                                                              FoodData Central.   
195   443341                                                                                          Validate Causative Mutations in Agriculturally-Important Vertebrates.   
196   443351                                                                                      Enhancing Insect Ecosystem Services that Benefit Modern Cropping Systems.   
197   443381                Advancing Soil Health and Agricultural Performance to Promote Sustainable Intensification and Resilience of Northwest Dryland Cropping Systems.   
198   441253                                                Improving Air Quality, Soil Health and Nutrient Use Efficiency to Increase Northwest Agroecosystem Performance.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                Abstract                                                                                                                                                                                                                                                                                                                                                                                                                                                     

In [60]:
# Drop decision column
finalnewarticlesdf = newarticlesdf.drop(['decision'], axis=1)
finalnewarticlesdf.set_index('Accession', inplace=True)
# finalnewarticlesdf.to_csv('out/newarticles4annotation23.csv')
print('\nSUMMARY\nCount of unique Accession numbers:')

print(finalnewarticlesdf.index.value_counts().sum())

display(finalnewarticlesdf)


SUMMARY
Count of unique Accession numbers:
8


Title                                                                              \
Accession                                                                                                                                                                
442616                                                                      Intervention Strategies to Control Salmonella and Campylobacter During Poultry Processing.   
443180     Enhancing Genetic Resistance and Vaccinal Response to Control MarekÎÃÃs Disease, Infectious Laryngotracheitis, and Infectious Bursal Disease in Chicken.   
443259                                                 Reducing the Impact of Subclinical Enteric Infections on Performance and Gastrointestinal Function of Broilers.   
443340                                                                                                                                               FoodData Central.   
443341                                                                                           Validate Causative Mutations in Agriculturally-Important Vertebrates.   
443351                                                                                       Enhancing Insect Ecosystem Services that Benefit Modern Cropping Systems.   
443381                 Advancing Soil Health and Agricultural Performance to Promote Sustainable Intensification and Resilience of Northwest Dryland Cropping Systems.   
441253                                                 Improving Air Quality, Soil Health and Nutrient Use Efficiency to Increase Northwest Agroecosystem Performance.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                      Abstract                                                                                                                                                                                                                                                                                                                                                                                                  

In [61]:
import xml.etree.cElementTree as ET

for t in newarticlesdf.itertuples():
    root = ET.Element("cogito")
    doc = ET.SubElement(root, "doc")
    doc.set('id', str(t.Accession))
    
    ET.SubElement(ET.SubElement(doc, "content", zone="articleTitle"), "text", mimetype="text/plain").text = t.Title
    ET.SubElement(ET.SubElement(doc, "content", zone="Abstract"), "text", mimetype="text/plain").text = t.Abstract
    metadata = ET.SubElement(doc, "metadata")
    ET.SubElement(metadata, "a", name="language", value="English")
    metadata = ET.SubElement(doc, "metadata", zone="articleTitle")
    ET.SubElement(metadata, "a", name="language", value="English")
    metadata = ET.SubElement(doc, "metadata", zone="Abstract")
    ET.SubElement(metadata, "a", name="language", value="English")
    
    tree = ET.ElementTree(root)
    tree.write(str(t.Accession) + ".cogx")